# **앙상블 영어 감정분석 모델**

본 영어 감정분석 모델은 고려대학교 디지털금융공학과 DFE610 디지털금융공학을 위한 자연어처리기술 수업의 과제를 수행하기 위해 개발한 모델이다.

본 앙상블 영어 감정분석 모델은 ELECTRA 모델과 '네이버 영화리뷰 감정분석 with Hugging Face BERT' 모델을 오픈소스를 참고하여 구성하였다.

본 모델은 ELECTRA, BERT의 아웃풋을 Soft Voting하여 최종 아웃풋을 산출한다.


1.   모델의 오픈소스 참고 출처
- 모델의 오픈소스 참고 출처

> ELECTRA를 이용한 감정분석 모델 : https://github.com/jiwonny/nlp_emotion_classification

> 네이버 영화리뷰 감정분석 with Hugging Face BERT : https://colab.research.google.com/drive/13AMh8N9tEIw5rmxgc1fQfS8581mWegxj


2. 상세사항
- 아래 깃허브의 Readme.md 확인

  https://github.com/yklove1025/Ensamble-Sentiment-Analysis-for-Korean

3. 실행환경
- 본 소스는 구글 Colab에서 작성됨 
- 본 소스의 실행을 위해서는 Colab Pro 환경이 필요(GPU 메모리 필요)
- ① 실행 후 ② 순차 실행 → 종료 후 ③ 실행 (실행순번 표기)
- BERT 모델 저장 후 업로드 시에도 메모리 문제 발생 가능함(재실행 권장) 


**Hugging Face의 Transformer Model 설치 ①,②**

In [1]:
!pip install transformers

     |████████████████████████████████| 1.5MB 5.9MB/s 
     |████████████████████████████████| 2.9MB 51.0MB/s 
     |████████████████████████████████| 890kB 49.3MB/s 
  Created wheel for sacremoses: filename=sacremoses-0.0.43-cp36-none-any.whl size=893261 sha256=06c50fa4e89d85ede0d7937110c7a4a5eef2a7e87278ed7c0db0eae2c9ce2c3f
  Stored in directory: /root/.cache/pip/wheels/29/3c/fd/7ce5c3f0666dab31a50123635e6fb5e19ceb42ce38d4e58f45
Successfully built sacremoses


**학습 데이터 - 트레이닝/테스트 파일 업로드 ①,②**

In [2]:
from google.colab import files
files.upload()
# Friends training, dev, test 파일 로컬 pc에서 업로드

Saving friends_dev.json to friends_dev.json
Saving friends_test.json to friends_test.json
Saving friends_train.json to friends_train.json


{'friends_dev.json': b'[\n    [\n        {\n            "speaker": "Phoebe",\n            "utterance": "Oh my God, he\\u0092s lost it. He\\u0092s totally lost it.",\n            "emotion": "non-neutral",\n            "annotation": "0002120"\n        },\n        {\n            "speaker": "Monica",\n            "utterance": "What?",\n            "emotion": "surprise",\n            "annotation": "1000130"\n        },\n        {\n            "speaker": "Ross",\n            "utterance": "Or! Or, we could go to the bank, close our accounts and cut them off at the source.",\n            "emotion": "neutral",\n            "annotation": "3000200"\n        },\n        {\n            "speaker": "Chandler",\n            "utterance": "You\\u0092re a genius!",\n            "emotion": "joy",\n            "annotation": "0500000"\n        },\n        {\n            "speaker": "Joey",\n            "utterance": "Aww, man, now we won\\u0092t be bank buddies!",\n            "emotion": "sadness",\n         

**공통 패키지 Import ①,②**

In [3]:
import pandas as pd
import numpy as np
import random
import time
import datetime
import torch
import tensorflow as tf
import keras
import os
import nltk
import matplotlib.pyplot as plt
import json
import re

from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.preprocessing.text import Tokenizer

from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler

from sklearn.model_selection import train_test_split
from sklearn.ensemble import BaggingClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import GaussianNB
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.metrics import accuracy_score, recall_score, precision_score, f1_score

from transformers import BertTokenizer
from transformers import ElectraTokenizer, ElectraForSequenceClassification
from transformers import BertForSequenceClassification, AdamW, BertConfig
from transformers import get_linear_schedule_with_warmup

from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.preprocessing.text import Tokenizer

from keras.models import Sequential
from keras import layers
from keras.models import Model
from keras.models import load_model
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.layers.core import Dense, SpatialDropout1D 
from keras.layers.convolutional import Conv1D 
from keras.layers.embeddings import Embedding
from keras.layers.pooling import GlobalMaxPooling1D
from keras.layers import LSTM
from keras.models import Sequential 
from keras.utils import np_utils 

from nltk.corpus import stopwords
from nltk.tag import pos_tag
from nltk.tokenize import word_tokenize
from nltk import Text

import collections

from collections import OrderedDict

from pprint import pprint

**데이터 로드 ①,②** 

In [4]:
with open('./friends_train.json', encoding = 'utf-8', mode = 'r') as json_file:
    json_train = json.load(json_file)
with open('./friends_dev.json', encoding = 'utf-8', mode = 'r') as json_file:
    json_dev = json.load(json_file)
with open('./friends_test.json', encoding = 'utf-8', mode = 'r') as json_file:
    json_test = json.load(json_file)

print(json_train)
print(np.shape(json_train))
print(json_dev)
print(np.shape(json_dev))
print(json_test)
print(np.shape(json_test))

[[{'speaker': 'Chandler', 'utterance': 'also I was the point person on my company\x92s transition from the KL-5 to GR-6 system.', 'emotion': 'neutral', 'annotation': '4100000'}, {'speaker': 'The Interviewer', 'utterance': 'You must\x92ve had your hands full.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'That I did. That I did.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'The Interviewer', 'utterance': 'So let\x92s talk a little bit about your duties.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'My duties?  All right.', 'emotion': 'surprise', 'annotation': '2000030'}, {'speaker': 'The Interviewer', 'utterance': 'Now you\x92ll be heading a whole division, so you\x92ll have a lot of duties.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'I see.', 'emotion': 'neutral', 'annotation': '3100010'}, {'speaker': 'The Interviewer', 'utterance': 'But there\

/usr/local/lib/python3.6/dist-packages/numpy/core/_asarray.py:83: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  return array(a, dtype, copy=False, order=order)


**테스트, 트레이닝 변수 선언 ①,②**

In [5]:
train_data = []
test_data = []

**트레이닝, 테스트 데이터 ①,②**

In [6]:
for rows in json_train:
    for row in rows:
        train_data.append(row)
for rows in json_dev:
    for row in rows:
        test_data.append(row)
for rows in json_test:
    for row in rows:
        train_data.append(row)

print(train_data)
print(np.shape(train_data))
print(test_data)
print(np.shape(test_data))

[{'speaker': 'Chandler', 'utterance': 'also I was the point person on my company\x92s transition from the KL-5 to GR-6 system.', 'emotion': 'neutral', 'annotation': '4100000'}, {'speaker': 'The Interviewer', 'utterance': 'You must\x92ve had your hands full.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'That I did. That I did.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'The Interviewer', 'utterance': 'So let\x92s talk a little bit about your duties.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'My duties?  All right.', 'emotion': 'surprise', 'annotation': '2000030'}, {'speaker': 'The Interviewer', 'utterance': 'Now you\x92ll be heading a whole division, so you\x92ll have a lot of duties.', 'emotion': 'neutral', 'annotation': '5000000'}, {'speaker': 'Chandler', 'utterance': 'I see.', 'emotion': 'neutral', 'annotation': '3100010'}, {'speaker': 'The Interviewer', 'utterance': 'But there\x

**트레이닝, 테스트 데이터 문장만 추출 ①,②**

In [7]:
train = []
test = []

In [8]:
for sentences in train_data :
  train.append(sentences['utterance'])

print(train[:5])
print(np.shape(train))

['also I was the point person on my company\x92s transition from the KL-5 to GR-6 system.', 'You must\x92ve had your hands full.', 'That I did. That I did.', 'So let\x92s talk a little bit about your duties.', 'My duties?  All right.']
(13325,)


In [9]:
for sentences in test_data :
  test.append(sentences['utterance'])

print(test[:5])
print(np.shape(test))

['Oh my God, he\x92s lost it. He\x92s totally lost it.', 'What?', 'Or! Or, we could go to the bank, close our accounts and cut them off at the source.', 'You\x92re a genius!', 'Aww, man, now we won\x92t be bank buddies!']
(1178,)


**ELECTRA, BERT 텍스트 전처리 ①,②**

In [10]:
sentences = train

X_train_bert_in = ["[CLS] " + str(sentence) + " [SEP]" for sentence in sentences]
X_train_bert_in[:10]

['[CLS] also I was the point person on my company\x92s transition from the KL-5 to GR-6 system. [SEP]',
 '[CLS] You must\x92ve had your hands full. [SEP]',
 '[CLS] That I did. That I did. [SEP]',
 '[CLS] So let\x92s talk a little bit about your duties. [SEP]',
 '[CLS] My duties?  All right. [SEP]',
 '[CLS] Now you\x92ll be heading a whole division, so you\x92ll have a lot of duties. [SEP]',
 '[CLS] I see. [SEP]',
 '[CLS] But there\x92ll be perhaps 30 people under you so you can dump a certain amount on them. [SEP]',
 '[CLS] Good to know. [SEP]',
 '[CLS] We can go into detail [SEP]']

In [11]:
sentences = test

X_test_bert_in = ["[CLS] " + str(sentence) + " [SEP]" for sentence in sentences]
X_test_bert_in[:10]

['[CLS] Oh my God, he\x92s lost it. He\x92s totally lost it. [SEP]',
 '[CLS] What? [SEP]',
 '[CLS] Or! Or, we could go to the bank, close our accounts and cut them off at the source. [SEP]',
 '[CLS] You\x92re a genius! [SEP]',
 '[CLS] Aww, man, now we won\x92t be bank buddies! [SEP]',
 '[CLS] Now, there\x92s two reasons. [SEP]',
 '[CLS] Hey. [SEP]',
 '[CLS] Hey! [SEP]',
 '[CLS] Ohh, you guys, remember that cute client I told you about? I bit him. [SEP]',
 '[CLS] Where?! [SEP]']

**레이블 처리 ①,②**

In [12]:
def labeltoint(str):
    return {'non-neutral': 0,
             'neutral': 1, 
             'joy': 2,
             'sadness': 3,
             'fear': 4,
             'anger': 5,
             'surprise': 6,
             'disgust': 7}[str]

labels_tr = []
labels_te = []

for d in train_data:
  labels_tr.append(labeltoint(d['emotion']))


for d in test_data:
  labels_te.append(labeltoint(d['emotion']))

print(labels_tr[:20])
print(labels_te[:20])

[1, 1, 1, 1, 6, 1, 1, 1, 1, 1, 4, 1, 6, 1, 6, 0, 6, 0, 1, 1]
[0, 6, 1, 2, 3, 1, 1, 2, 1, 6, 1, 1, 6, 0, 1, 2, 1, 1, 1, 6]


In [13]:
labels_train = np.array(labels_tr)
labels_test = np.array(labels_te)

In [14]:
print(labels_train)
print(labels_test)
print(len(labels_train))
print(len(labels_test))

[1 1 1 ... 1 1 1]
[0 6 1 ... 3 3 3]
13325
1178


**ELECTRA 감정분석 데이터 처리 ①**

In [15]:
tokenizer = ElectraTokenizer.from_pretrained('google/electra-large-discriminator')
#tokenizer = ElectraTokenizer.from_pretrained('google/electra-large-generator')
  
X_train_tokenized_text = [tokenizer.tokenize(sent) for sent in X_train_bert_in]
X_test_tokenized_text = [tokenizer.tokenize(sent) for sent in X_test_bert_in]

print (X_train_tokenized_text[0])
print (X_test_tokenized_text[0])

MAX_LEN = 85

# 토큰을 숫자 인덱스로 변환
X_train_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_train_tokenized_text]
X_test_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_test_tokenized_text]

X_train_bert = pad_sequences(X_train_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")
X_test_bert = pad_sequences(X_test_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")


['[CLS]', 'also', 'i', 'was', 'the', 'point', 'person', 'on', 'my', 'company', '##s', 'transition', 'from', 'the', 'k', '##l', '-', '5', 'to', 'gr', '-', '6', 'system', '.', '[SEP]']
['[CLS]', 'oh', 'my', 'god', ',', 'he', '##s', 'lost', 'it', '.', 'he', '##s', 'totally', 'lost', 'it', '.', '[SEP]']


**ELECTRA 감정분석 모델 설정 ①**

In [16]:
# 어텐션 마스크 초기화
attention_masks = []

# 어텐션 마스크를 패딩이 아니면 1, 패딩이면 0으로 설정
# 패딩 부분은 BERT 모델에서 어텐션을 수행하지 않아 속도 향상
for seq in X_train_bert:
    seq_mask = [float(i>0) for i in seq]
    attention_masks.append(seq_mask)

print(attention_masks[0])

# 훈련셋과 검증셋으로 분리
train_inputs, validation_inputs, train_labels, validation_labels = train_test_split(X_train_bert,
                                                                                    labels_train, 
                                                                                    random_state=2018, 
                                                                                    test_size=0.2)

# 어텐션 마스크를 훈련셋과 검증셋으로 분리
train_masks, validation_masks, _, _ = train_test_split(attention_masks, 
                                                       X_train_bert,
                                                       random_state=2018, 
                                                       test_size=0.2)

# 데이터를 파이토치의 텐서로 변환
train_inputs = torch.tensor(train_inputs)
train_labels = torch.tensor(train_labels)
train_masks = torch.tensor(train_masks)
validation_inputs = torch.tensor(validation_inputs)
validation_labels = torch.tensor(validation_labels)
validation_masks = torch.tensor(validation_masks)				

attention_masks = []

for seq in X_test_bert:
    seq_mask = [float(i>0) for i in seq]
    attention_masks.append(seq_mask)

test_inputs = torch.tensor(X_test_bert)
test_labels = torch.tensor(labels_test)
test_masks = torch.tensor(attention_masks)

[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


In [17]:
# 배치 사이즈
batch_size = 32

# 파이토치의 DataLoader로 입력, 마스크, 라벨을 묶어 데이터 설정
# 학습시 배치 사이즈 만큼 데이터를 가져옴
train_data = TensorDataset(train_inputs, train_masks, train_labels)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

validation_data = TensorDataset(validation_inputs, validation_masks, validation_labels)
validation_sampler = SequentialSampler(validation_data)
validation_dataloader = DataLoader(validation_data, sampler=validation_sampler, batch_size=batch_size)

test_data = TensorDataset(test_inputs, test_masks, test_labels)
test_sampler = RandomSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=test_sampler, batch_size=batch_size)

In [18]:
# GPU 디바이스 이름 구함
device_name = tf.test.gpu_device_name()

# GPU 디바이스 이름 검사
if device_name == '/device:GPU:0':
    print('Found GPU at: {}'.format(device_name))
else:
    raise SystemError('GPU device not found')

Found GPU at: /device:GPU:0


In [19]:
# 디바이스 설정
if torch.cuda.is_available():    
    device = torch.device("cuda")
    print('There are %d GPU(s) available.' % torch.cuda.device_count())
    print('We will use the GPU:', torch.cuda.get_device_name(0))
else:
    device = torch.device("cpu")
    print('No GPU available, using the CPU instead.')

There are 1 GPU(s) available.
We will use the GPU: Tesla P100-PCIE-16GB


In [20]:
# 분류를 위한 ELECTRA 모델 생성
#model = ElectraForSequenceClassification.from_pretrained('google/electra-large-generator', num_labels=8)
#model = ElectraForSequenceClassification.from_pretrained('google/electra-small-generator', num_labels=8)
model = ElectraForSequenceClassification.from_pretrained('google/electra-large-discriminator', num_labels=8)
model.cuda()

Some weights of the model checkpoint at google/electra-large-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.weight', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at google/electra-large-discriminator and are newly initialized: ['classifier

ElectraForSequenceClassification(
  (electra): ElectraModel(
    (embeddings): ElectraEmbeddings(
      (word_embeddings): Embedding(30522, 1024, padding_idx=0)
      (position_embeddings): Embedding(512, 1024)
      (token_type_embeddings): Embedding(2, 1024)
      (LayerNorm): LayerNorm((1024,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): ElectraEncoder(
      (layer): ModuleList(
        (0): ElectraLayer(
          (attention): ElectraAttention(
            (self): ElectraSelfAttention(
              (query): Linear(in_features=1024, out_features=1024, bias=True)
              (key): Linear(in_features=1024, out_features=1024, bias=True)
              (value): Linear(in_features=1024, out_features=1024, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): ElectraSelfOutput(
              (dense): Linear(in_features=1024, out_features=1024, bias=True)
              (LayerNorm

In [21]:
# 옵티마이저 설정
optimizer = AdamW(model.parameters(),
                  lr = 2e-5, 
                  eps = 1e-8
                )

epochs = 5

# 총 훈련 스텝 : 배치반복 횟수 * 에폭
total_steps = len(train_dataloader) * epochs

# 학습률을 조금씩 감소시키는 스케줄러 생성
scheduler = get_linear_schedule_with_warmup(optimizer, 
                                            num_warmup_steps = 0,
                                            num_training_steps = total_steps)

In [22]:
from sklearn.metrics import f1_score

# 정확도 계산 함수
def flat_accuracy(preds, labels):
    pred_flat = np.argmax(preds, axis=1).flatten()
    labels_flat = labels.flatten()

    return np.sum(pred_flat == labels_flat) / len(labels_flat)


def getF1Score(preds, labels):
  pred_flat = np.argmax(preds, axis=1).flatten()
  labels_flat = labels.flatten()

  return f1_score(labels_flat, pred_flat, average = None)

In [23]:
# 시간 표시 함수
def format_time(elapsed):

    # 반올림
    elapsed_rounded = int(round((elapsed)))
    
    # hh:mm:ss으로 형태 변경
    return str(datetime.timedelta(seconds=elapsed_rounded))

**ELECTRA 감정분석 모델 학습 실행 ①**

In [24]:
seed_val = 42
random.seed(seed_val)
np.random.seed(seed_val)
torch.manual_seed(seed_val)
torch.cuda.manual_seed_all(seed_val)

model.zero_grad()

# 에폭만큼 반복
for epoch_i in range(0, epochs):
    
    # ========================================
    #               Training
    # ========================================
    
    print("")
    print('======== Epoch {:} / {:} ========'.format(epoch_i + 1, epochs))
    print('Training...')

    t0 = time.time()
    total_loss = 0
    model.train()
        
    # 데이터로더에서 배치만큼 반복하여 가져옴
    for step, batch in enumerate(train_dataloader):
        if step % 500 == 0 and not step == 0:
            elapsed = format_time(time.time() - t0)
            print('  Batch {:>5,}  of  {:>5,}.    Elapsed: {:}.'.format(step, len(train_dataloader), elapsed))

        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch
             
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask, 
                        labels=b_labels)

        loss = outputs[0]
        total_loss += loss.item()


        loss.backward()

        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        optimizer.step()
        scheduler.step()
        model.zero_grad()

    # 평균 로스 계산
    avg_train_loss = total_loss / len(train_dataloader)            

    print("")
    print("  Average training loss: {0:.2f}".format(avg_train_loss))
    print("  Training epcoh took: {:}".format(format_time(time.time() - t0)))
        
    # ========================================
    #               Validation
    # ========================================

    print("")
    print("Running Validation...")

    t0 = time.time()
    model.eval()
    eval_loss, eval_accuracy, eval_f1 = 0, 0, 0
    nb_eval_steps, nb_eval_examples = 0, 0

    # 데이터로더에서 배치만큼 반복하여 가져옴
    for batch in validation_dataloader:
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch

        with torch.no_grad():     
            outputs = model(b_input_ids, 
                            token_type_ids=None, 
                            attention_mask=b_input_mask)
        
        logits = outputs[0]
        logits = logits.detach().cpu().numpy()
        label_ids = b_labels.to('cpu').numpy()
     
        tmp_eval_accuracy = flat_accuracy(logits, label_ids)
        # tmp_eval_f1 = getF1Score(logits, label_ids)
        eval_accuracy += tmp_eval_accuracy
        # eval_f1 += tmp_eval_f1
        nb_eval_steps += 1

    print("  Accuracy: {0:.2f}".format(eval_accuracy/nb_eval_steps))
    # print("  F1: {0:.2f}".format(eval_f1/nb_eval_steps))
    print("  Validation took: {:}".format(format_time(time.time() - t0)))

print("")
print("Training complete!")


======== Epoch 1 / 5 ========
Training...

  Average training loss: 1.42
  Training epcoh took: 0:05:11

Running Validation...
  Accuracy: 0.60
  Validation took: 0:00:24

======== Epoch 2 / 5 ========
Training...

  Average training loss: 1.07
  Training epcoh took: 0:05:11

Running Validation...
  Accuracy: 0.62
  Validation took: 0:00:24

======== Epoch 3 / 5 ========
Training...

  Average training loss: 0.88
  Training epcoh took: 0:05:11

Running Validation...
  Accuracy: 0.63
  Validation took: 0:00:24

======== Epoch 4 / 5 ========
Training...

  Average training loss: 0.71
  Training epcoh took: 0:05:11

Running Validation...
  Accuracy: 0.63
  Validation took: 0:00:24

======== Epoch 5 / 5 ========
Training...

  Average training loss: 0.59
  Training epcoh took: 0:05:11

Running Validation...
  Accuracy: 0.63
  Validation took: 0:00:24

Training complete!


**ELECTRA 감정분석 모델 테스트**

In [25]:
#시작 시간 설정
t0 = time.time()

# 평가모드로 변경
model.eval()

# 변수 초기화
eval_loss, eval_accuracy = 0, 0
nb_eval_steps, nb_eval_examples = 0, 0

# 데이터로더에서 배치만큼 반복하여 가져옴
for step, batch in enumerate(test_dataloader):
    # 경과 정보 표시
    if step % 100 == 0 and not step == 0:
        elapsed = format_time(time.time() - t0)
        print('  Batch {:>5,}  of  {:>5,}.    Elapsed: {:}.'.format(step, len(test_dataloader), elapsed))

    # 배치를 GPU에 넣음
    batch = tuple(t.to(device) for t in batch)
    
    # 배치에서 데이터 추출
    b_input_ids, b_input_mask, b_labels = batch
    
    # 그래디언트 계산 안함
    with torch.no_grad():     
        # Forward 수행
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask)
    
    # 로스 구함
    logits = outputs[0]

    # CPU로 데이터 이동
    logits = logits.detach().cpu().numpy()
    ELECTRA_output = []
    ELECTRA_output = ELECTRA_output.append(logits)
    label_ids = b_labels.to('cpu').numpy()
    
    # 출력 로짓과 라벨을 비교하여 정확도 계산
    tmp_eval_accuracy = flat_accuracy(logits, label_ids)
    eval_accuracy += tmp_eval_accuracy
    nb_eval_steps += 1

print("")
print("Accuracy: {0:.2f}".format(eval_accuracy/nb_eval_steps))
print("Test took: {:}".format(format_time(time.time() - t0)))


Accuracy: 0.60
Test took: 0:00:11


**ELECTRA 감정분석 모델 신규 텍스트 함수 선언 ①**

In [26]:
# 문장 테스트
def test_sentences(inputs, masks):

    # 평가모드로 변경
    model.eval()

    # 문장을 입력 데이터로 변환
    #inputs, masks = convert_input_data(sentences)
    inputs = inputs
    masks = masks

    # 데이터를 GPU에 넣음
    b_input_ids = inputs.to(device)
    b_input_mask = masks.to(device)
            
    # 그래디언트 계산 안함
    with torch.no_grad():     
        # Forward 수행
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask)

    # 로스 구함
    logits = outputs[0]

    # CPU로 데이터 이동
    logits = logits.detach().cpu().numpy()

    return logits

**ELECTRA를 이용한 감정분석 모델 테스트 Output 데이터 생성 ①**

- test 데이터 범위 지정 (GPU 사용량 관련 지정) ①

In [27]:
test_inputs_1 = test_inputs[:1178]
test_masks_1 = test_masks[:1178]

- 테스트 데이터로 예측 수행 ①

In [28]:
logits = test_sentences(test_inputs_1, test_masks_1)

x_predict_ELECTRA = []
x_predict_ELECTRA = logits

x_predict_ELECTRA_socre = []
x_predict_ELECTRA_socre = np.argmax(logits, axis = 1)
x_predict_ELECTRA_score = x_predict_ELECTRA_socre.tolist()

print(x_predict_ELECTRA)
print(x_predict_ELECTRA_score)

[[ 2.6085823  -2.2805457  -0.94423044 ...  0.6650286   0.6600782
   0.3880639 ]
 [ 0.90981543  2.7102852  -1.251963   ... -1.6308149   3.1304383
  -1.7211487 ]
 [ 3.2807395   0.1433224   1.279127   ...  0.05231008 -0.98728645
  -0.98805743]
 ...
 [ 0.06253487  0.04663825 -1.5110133  ... -0.8450888  -1.8365842
   0.1268996 ]
 [ 0.2725404  -0.21638295 -1.5622925  ... -0.8051849  -1.953074
   0.3009828 ]
 [ 3.0256608   0.5004839   2.5438282  ... -0.91475105  0.3191878
  -1.8501463 ]]
[0, 6, 0, 2, 0, 1, 1, 2, 0, 6, 1, 1, 0, 0, 1, 2, 1, 1, 1, 6, 6, 6, 2, 1, 1, 2, 6, 2, 1, 1, 1, 1, 1, 0, 1, 1, 6, 1, 6, 6, 6, 0, 5, 6, 3, 5, 1, 5, 0, 0, 1, 1, 5, 1, 1, 2, 1, 1, 1, 0, 1, 1, 1, 6, 6, 2, 2, 1, 1, 6, 2, 6, 0, 0, 2, 2, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 2, 1, 1, 2, 2, 1, 3, 1, 2, 1, 1, 0, 0, 1, 1, 0, 0, 5, 5, 6, 0, 6, 0, 1, 2, 1, 6, 0, 0, 1, 0, 1, 1, 5, 1, 5, 6, 2, 0, 1, 2, 6, 0, 6, 1, 5, 2, 2, 2, 2, 6, 1, 2, 2, 1, 6, 0, 1, 0, 6, 0, 0, 1, 1, 1, 1, 2, 1, 1, 1, 5, 0, 1, 0, 5, 6, 2, 0, 6, 1, 6, 1, 1, 7, 

- ELECTRA 모델 예측 결과 스코어링

In [29]:
print("ELECTRA model accuracy : ", accuracy_score(labels_test, x_predict_ELECTRA_score))

ELECTRA model accuracy :  0.597623089983022


- ELECTRA output csv 파일 저장 ①

In [30]:
ensemble_ELECTRA = pd.DataFrame(x_predict_ELECTRA)
print(ensemble_ELECTRA)

             0         1         2  ...         5         6         7
0     2.608582 -2.280546 -0.944230  ...  0.665029  0.660078  0.388064
1     0.909815  2.710285 -1.251963  ... -1.630815  3.130438 -1.721149
2     3.280740  0.143322  1.279127  ...  0.052310 -0.987286 -0.988057
3     0.783259 -0.891066  4.166071  ... -0.504811  0.606539 -1.515062
4     2.611266 -1.608976 -1.230531  ...  0.464994 -1.351587  0.510723
...        ...       ...       ...  ...       ...       ...       ...
1173  0.533923  5.039102 -1.392905  ... -2.280438 -1.098461 -1.214996
1174  1.126813 -0.879095 -1.802367  ... -0.715736 -1.506538  0.491429
1175  0.062535  0.046638 -1.511013  ... -0.845089 -1.836584  0.126900
1176  0.272540 -0.216383 -1.562292  ... -0.805185 -1.953074  0.300983
1177  3.025661  0.500484  2.543828  ... -0.914751  0.319188 -1.850146

[1178 rows x 8 columns]


In [31]:
ensemble_ELECTRA.to_csv('ensemble_ELECTRA_eng.csv')

- ELECTRA output 레이블 변환 파일 저장 ①

In [32]:
def inttolabel(str):
    return { 0 : 'non-neutral',
             1 : 'neutral', 
             2 : 'joy', 
             3 : 'sadness', 
             4 : 'fear', 
             5 : 'anger', 
             6 : 'surprise', 
             7 : 'disgust'}[str]

predicted_ELECTRA_str = []

for d in x_predict_ELECTRA_score:
  predicted_ELECTRA_str.append(inttolabel(d))

In [33]:
ensemble_ELECTRA_out = pd.DataFrame({'Expected' : predicted_ELECTRA_str})
print(ensemble_ELECTRA_out)

         Expected
0     non-neutral
1        surprise
2     non-neutral
3             joy
4     non-neutral
...           ...
1173      neutral
1174      sadness
1175      sadness
1176      sadness
1177  non-neutral

[1178 rows x 1 columns]


In [34]:
ensemble_ELECTRA_out.to_csv('ensemble_ELECTRA_eng_score.csv')

**BERT 감정분석 데이터 처리 ②**

- 변수 초기화

In [35]:
X_train_tokenized_text = []
X_test_tokenized_text = []
X_kaggle_tokenized_text = []
X_train_bert = []
X_test_bert = []
X_kaggle_bert = []
train_inputs = []
train_labels = []
train_masks = []
validation_inputs = []
validation_labels = []
validation_masks = []
test_inputs = []
test_labels = []
test_masks = []

In [36]:
tokenizer = BertTokenizer.from_pretrained('bert-base-multilingual-cased', do_lower_case=False)

X_train_tokenized_text = [tokenizer.tokenize(sent) for sent in X_train_bert_in]
X_test_tokenized_text = [tokenizer.tokenize(sent) for sent in X_test_bert_in]

print (X_train_tokenized_text[0])
print (X_test_tokenized_text[0])

# 입력 토큰의 최대 시퀀스 길이
MAX_LEN = 128

# 토큰을 숫자 인덱스로 변환
X_train_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_train_tokenized_text]
X_test_bert = [tokenizer.convert_tokens_to_ids(x) for x in X_test_tokenized_text]

# 문장을 MAX_LEN 길이에 맞게 자르고, 모자란 부분을 패딩 0으로 채움
X_train_bert = pad_sequences(X_train_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")
X_test_bert = pad_sequences(X_test_bert, maxlen=MAX_LEN, dtype="long", truncating="post", padding="post")


['[CLS]', 'also', 'I', 'was', 'the', 'point', 'person', 'on', 'my', 'company', '##s', 'transition', 'from', 'the', 'K', '##L', '-', '5', 'to', 'GR', '-', '6', 'system', '.', '[SEP]']
['[CLS]', 'Oh', 'my', 'God', ',', 'he', '##s', 'lost', 'it', '.', 'He', '##s', 'totally', 'lost', 'it', '.', '[SEP]']


**BERT 감정분석 모델 설정 ②**

In [37]:
# 어텐션 마스크 초기화
attention_masks = []

# 어텐션 마스크를 패딩이 아니면 1, 패딩이면 0으로 설정
# 패딩 부분은 BERT 모델에서 어텐션을 수행하지 않아 속도 향상
for seq in X_train_bert:
    seq_mask = [float(i>0) for i in seq]
    attention_masks.append(seq_mask)

print(attention_masks[0])

# 훈련셋과 검증셋으로 분리
train_inputs, validation_inputs, train_labels, validation_labels = train_test_split(X_train_bert,
                                                                                    labels_train, 
                                                                                    random_state=2018, 
                                                                                    test_size=0.1)

# 어텐션 마스크를 훈련셋과 검증셋으로 분리
train_masks, validation_masks, _, _ = train_test_split(attention_masks, 
                                                       X_train_bert,
                                                       random_state=2018, 
                                                       test_size=0.1)

# 데이터를 파이토치의 텐서로 변환
train_inputs = torch.tensor(train_inputs)
train_labels = torch.tensor(train_labels)
train_masks = torch.tensor(train_masks)
validation_inputs = torch.tensor(validation_inputs)
validation_labels = torch.tensor(validation_labels)
validation_masks = torch.tensor(validation_masks)				

attention_masks = []

for seq in X_test_bert:
    seq_mask = [float(i>0) for i in seq]
    attention_masks.append(seq_mask)

test_inputs = torch.tensor(X_test_bert)
test_labels = torch.tensor(labels_test)
test_masks = torch.tensor(attention_masks)

[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


In [38]:
# 배치 사이즈
batch_size = 32

# 파이토치의 DataLoader로 입력, 마스크, 라벨을 묶어 데이터 설정
# 학습시 배치 사이즈 만큼 데이터를 가져옴
train_data = TensorDataset(train_inputs, train_masks, train_labels)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

validation_data = TensorDataset(validation_inputs, validation_masks, validation_labels)
validation_sampler = SequentialSampler(validation_data)
validation_dataloader = DataLoader(validation_data, sampler=validation_sampler, batch_size=batch_size)

test_data = TensorDataset(test_inputs, test_masks, test_labels)
test_sampler = RandomSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=test_sampler, batch_size=batch_size)

In [39]:
# GPU 디바이스 이름 구함
device_name = tf.test.gpu_device_name()

# GPU 디바이스 이름 검사
if device_name == '/device:GPU:0':
    print('Found GPU at: {}'.format(device_name))
else:
    raise SystemError('GPU device not found')

Found GPU at: /device:GPU:0


In [40]:
# 디바이스 설정
if torch.cuda.is_available():    
    device = torch.device("cuda")
    print('There are %d GPU(s) available.' % torch.cuda.device_count())
    print('We will use the GPU:', torch.cuda.get_device_name(0))
else:
    device = torch.device("cpu")
    print('No GPU available, using the CPU instead.')

There are 1 GPU(s) available.
We will use the GPU: Tesla P100-PCIE-16GB


In [41]:
# 분류를 위한 BERT 모델 생성
model = BertForSequenceClassification.from_pretrained("bert-base-multilingual-cased", num_labels=8)
model.cuda()

Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing BertForSequenceClassification: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model ch

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(119547, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elemen

In [42]:
# 옵티마이저 설정
optimizer = AdamW(model.parameters(),
                  lr = 2e-5, # 학습률
                  eps = 1e-8 # 0으로 나누는 것을 방지하기 위한 epsilon 값
                )

# 에폭수
epochs = 5

# 총 훈련 스텝 : 배치반복 횟수 * 에폭
total_steps = len(train_dataloader) * epochs

# 처음에 학습률을 조금씩 변화시키는 스케줄러 생성
scheduler = get_linear_schedule_with_warmup(optimizer, 
                                            num_warmup_steps = 0,
                                            num_training_steps = total_steps)

In [43]:
from sklearn.metrics import f1_score

# 정확도 계산 함수
def flat_accuracy(preds, labels):
    pred_flat = np.argmax(preds, axis=1).flatten()
    labels_flat = labels.flatten()

    return np.sum(pred_flat == labels_flat) / len(labels_flat)


def getF1Score(preds, labels):
  pred_flat = np.argmax(preds, axis=1).flatten()
  labels_flat = labels.flatten()

  return f1_score(labels_flat, pred_flat, average = None)

In [44]:
# 시간 표시 함수
def format_time(elapsed):

    # 반올림
    elapsed_rounded = int(round((elapsed)))
    
    # hh:mm:ss으로 형태 변경
    return str(datetime.timedelta(seconds=elapsed_rounded))

**BERT 감정분석 모델 학습 실행 ②**

In [45]:
seed_val = 42
random.seed(seed_val)
np.random.seed(seed_val)
torch.manual_seed(seed_val)
torch.cuda.manual_seed_all(seed_val)

model.zero_grad()

# 에폭만큼 반복
for epoch_i in range(0, epochs):
    
    # ========================================
    #               Training
    # ========================================
    
    print("")
    print('======== Epoch {:} / {:} ========'.format(epoch_i + 1, epochs))
    print('Training...')

    t0 = time.time()
    total_loss = 0
    model.train()
        
    # 데이터로더에서 배치만큼 반복하여 가져옴
    for step, batch in enumerate(train_dataloader):
        if step % 500 == 0 and not step == 0:
            elapsed = format_time(time.time() - t0)
            print('  Batch {:>5,}  of  {:>5,}.    Elapsed: {:}.'.format(step, len(train_dataloader), elapsed))

        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch
             
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask, 
                        labels=b_labels)

        loss = outputs[0]
        total_loss += loss.item()


        loss.backward()

        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)
        optimizer.step()
        scheduler.step()
        model.zero_grad()

    # 평균 로스 계산
    avg_train_loss = total_loss / len(train_dataloader)            

    print("")
    print("  Average training loss: {0:.2f}".format(avg_train_loss))
    print("  Training epcoh took: {:}".format(format_time(time.time() - t0)))
        
    # ========================================
    #               Validation
    # ========================================

    print("")
    print("Running Validation...")

    t0 = time.time()
    model.eval()
    eval_loss, eval_accuracy, eval_f1 = 0, 0, 0
    nb_eval_steps, nb_eval_examples = 0, 0

    # 데이터로더에서 배치만큼 반복하여 가져옴
    for batch in validation_dataloader:
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_mask, b_labels = batch

        with torch.no_grad():     
            outputs = model(b_input_ids, 
                            token_type_ids=None, 
                            attention_mask=b_input_mask)
        
        logits = outputs[0]
        logits = logits.detach().cpu().numpy()
        label_ids = b_labels.to('cpu').numpy()
     
        tmp_eval_accuracy = flat_accuracy(logits, label_ids)
        # tmp_eval_f1 = getF1Score(logits, label_ids)
        eval_accuracy += tmp_eval_accuracy
        # eval_f1 += tmp_eval_f1
        nb_eval_steps += 1

    print("  Accuracy: {0:.2f}".format(eval_accuracy/nb_eval_steps))
    # print("  F1: {0:.2f}".format(eval_f1/nb_eval_steps))
    print("  Validation took: {:}".format(format_time(time.time() - t0)))

print("")
print("Training complete!")


======== Epoch 1 / 5 ========
Training...

  Average training loss: 1.33
  Training epcoh took: 0:02:36

Running Validation...
  Accuracy: 0.56
  Validation took: 0:00:05

======== Epoch 2 / 5 ========
Training...

  Average training loss: 1.13
  Training epcoh took: 0:02:35

Running Validation...
  Accuracy: 0.58
  Validation took: 0:00:05

======== Epoch 3 / 5 ========
Training...

  Average training loss: 1.00
  Training epcoh took: 0:02:36

Running Validation...
  Accuracy: 0.57
  Validation took: 0:00:05

======== Epoch 4 / 5 ========
Training...

  Average training loss: 0.88
  Training epcoh took: 0:02:36

Running Validation...
  Accuracy: 0.57
  Validation took: 0:00:05

======== Epoch 5 / 5 ========
Training...

  Average training loss: 0.79
  Training epcoh took: 0:02:36

Running Validation...
  Accuracy: 0.56
  Validation took: 0:00:05

Training complete!


**BERT 감정분석 모델 테스트**

In [46]:
#시작 시간 설정
t0 = time.time()

# 평가모드로 변경
model.eval()

# 변수 초기화
eval_loss, eval_accuracy = 0, 0
nb_eval_steps, nb_eval_examples = 0, 0

# 데이터로더에서 배치만큼 반복하여 가져옴
for step, batch in enumerate(test_dataloader):
    # 경과 정보 표시
    if step % 100 == 0 and not step == 0:
        elapsed = format_time(time.time() - t0)
        print('  Batch {:>5,}  of  {:>5,}.    Elapsed: {:}.'.format(step, len(test_dataloader), elapsed))

    # 배치를 GPU에 넣음
    batch = tuple(t.to(device) for t in batch)
    
    # 배치에서 데이터 추출
    b_input_ids, b_input_mask, b_labels = batch
    
    # 그래디언트 계산 안함
    with torch.no_grad():     
        # Forward 수행
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask)
    
    # 로스 구함
    logits = outputs[0]

    # CPU로 데이터 이동
    logits = logits.detach().cpu().numpy()
    label_ids = b_labels.to('cpu').numpy()
    
    # 출력 로짓과 라벨을 비교하여 정확도 계산
    tmp_eval_accuracy = flat_accuracy(logits, label_ids)
    eval_accuracy += tmp_eval_accuracy
    nb_eval_steps += 1

print("")
print("Accuracy: {0:.2f}".format(eval_accuracy/nb_eval_steps))
print("Test took: {:}".format(format_time(time.time() - t0)))


Accuracy: 0.56
Test took: 0:00:05


**BERT 감정분석 모델 신규 텍스트 함수 선언 ②**

In [47]:
# 문장 테스트
def test_sentences(inputs, masks):

    # 평가모드로 변경
    model.eval()

    # 문장을 입력 데이터로 변환
    #inputs, masks = convert_input_data(sentences)
    inputs = inputs
    masks = masks

    # 데이터를 GPU에 넣음
    b_input_ids = inputs.to(device)
    b_input_mask = masks.to(device)
            
    # 그래디언트 계산 안함
    with torch.no_grad():     
        # Forward 수행
        outputs = model(b_input_ids, 
                        token_type_ids=None, 
                        attention_mask=b_input_mask)

    # 로스 구함
    logits = outputs[0]

    # CPU로 데이터 이동
    logits = logits.detach().cpu().numpy()

    return logits

**BERT를 이용한 감정분석 모델 테스트 Output 데이터 생성 ②**

- test 데이터 범위 지정 (GPU 사용량 관련 지정) ②

In [48]:
test_inputs_1 = test_inputs[:1178]
test_masks_1 = test_masks[:1178]

- 테스트 데이터로 예측 수행 ②

In [49]:
logits = test_sentences(test_inputs_1, test_masks_1)

x_predict_BERT_1 = []
x_predict_BERT_1 = logits

x_predict_BERT_socre_1 = []
x_predict_BERT_socre_1 = np.argmax(logits, axis = 1)
x_predict_BERT_score_1 = x_predict_BERT_socre_1.tolist()

print(x_predict_BERT_1)
print(x_predict_BERT_score_1)

[[ 1.6739748e+00 -2.4837942e+00 -8.4733379e-01 ...  1.2789099e-02
   1.2195185e+00 -3.9735507e-02]
 [ 5.2667737e-01  3.1373818e+00 -1.5046971e+00 ... -1.5744133e+00
   3.2262819e+00 -1.1507061e+00]
 [ 2.4261825e+00  7.6291037e-01  1.8651817e+00 ...  8.4679663e-01
  -2.1793985e-01 -9.1320747e-01]
 ...
 [ 7.8944492e-01 -9.2737925e-01 -7.8025806e-01 ...  4.7843748e-01
  -2.0705175e+00 -4.5532104e-01]
 [ 2.2300475e+00 -1.5829986e+00 -1.0264909e+00 ...  1.4660726e+00
  -3.0813646e-01  2.4866093e-02]
 [ 2.7908175e+00  8.5621029e-01  1.9522923e+00 ... -1.2947045e-03
   1.6100378e+00 -1.5803977e+00]]
[0, 6, 0, 2, 0, 1, 1, 2, 0, 6, 1, 1, 0, 3, 1, 2, 2, 1, 1, 0, 5, 6, 2, 1, 1, 2, 6, 2, 1, 1, 1, 1, 1, 0, 1, 1, 6, 1, 1, 6, 1, 1, 0, 6, 1, 1, 1, 1, 3, 1, 1, 1, 0, 2, 2, 2, 1, 2, 2, 2, 1, 1, 1, 6, 5, 2, 2, 1, 1, 1, 2, 1, 1, 2, 2, 2, 6, 0, 0, 0, 1, 1, 1, 1, 0, 1, 1, 2, 0, 0, 1, 2, 1, 0, 1, 2, 1, 1, 0, 0, 1, 1, 0, 0, 0, 0, 6, 5, 1, 1, 1, 2, 6, 0, 1, 3, 1, 0, 1, 1, 5, 1, 5, 1, 2, 0, 1, 2, 6, 0, 6, 1, 3, 

- BERT 모델 예측 결과 스코어링 ②

In [50]:
print("BERT model accuracy : ", accuracy_score(labels_test, x_predict_BERT_score_1))

BERT model accuracy :  0.5611205432937182


**BERT 예측결과 CSV 파일 저장 ②**

In [51]:
ensemble_BERT_eng_out = pd.DataFrame(x_predict_BERT_1)
print(ensemble_BERT_eng_out)

             0         1         2  ...         5         6         7
0     1.673975 -2.483794 -0.847334  ...  0.012789  1.219519 -0.039736
1     0.526677  3.137382 -1.504697  ... -1.574413  3.226282 -1.150706
2     2.426183  0.762910  1.865182  ...  0.846797 -0.217940 -0.913207
3     1.445673 -1.322713  3.538973  ...  0.580931  1.252362 -0.876142
4     2.210606 -0.715883  2.017992  ... -0.558688 -0.802268 -0.499576
...        ...       ...       ...  ...       ...       ...       ...
1173  0.937616  4.649868 -1.314408  ... -1.445912 -2.046066 -0.676416
1174  1.791245 -2.425448 -0.514695  ...  0.217908  2.127723 -0.352204
1175  0.789445 -0.927379 -0.780258  ...  0.478437 -2.070518 -0.455321
1176  2.230047 -1.582999 -1.026491  ...  1.466073 -0.308136  0.024866
1177  2.790817  0.856210  1.952292  ... -0.001295  1.610038 -1.580398

[1178 rows x 8 columns]


In [52]:
ensemble_BERT_eng_out.to_csv('ensemble_BERT_eng.csv')

**앙상블 예측 결과 산출 ③**

- ELECTRA(ensemble_ELECTRA_eng.csv), BERT(ensemble_BERT_eng.csv) 파일 로컬 PC에서 업로드 (필요시) ③

In [ ]:
from google.colab import files
files.upload()

Saving ensemble_ELECTRA_eng.csv to ensemble_ELECTRA_eng.csv
Saving ensemble_ELECTRA_eng_score.csv to ensemble_ELECTRA_eng_score.csv


{'ensemble_ELECTRA_eng.csv': b',0,1,2,3,4,5,6,7\n0,1.1211046,2.7688286,-0.2632175,-1.5233626,-1.6259078,-0.45164964,1.1357635,-1.6544173\n1,1.4984092,1.8670492,-0.45305726,-0.74367005,-1.2299558,-0.13911106,0.50906956,-1.142723\n2,0.99663943,3.1049674,-0.30291656,-1.271197,-1.4858508,-0.2886291,0.6301598,-1.5203601\n3,0.80247664,2.0479035,-0.6879075,-1.4397459,-1.3773036,-0.44799155,1.6505023,-1.4094748\n4,1.6276816,2.4731748,0.44665658,-0.5903233,-1.2706581,0.029513763,-0.99988776,-1.1007862\n5,1.1046484,0.054736648,-0.3413722,-0.31704414,-0.84785604,-0.07381424,0.93185055,-0.44610545\n6,1.5368716,1.4430028,1.9831098,-0.9922139,-1.4805876,-0.25466463,-0.64088076,-1.332823\n7,1.1249743,3.2403696,1.5041434,-1.4588739,-1.6799097,-0.61506385,-0.4509177,-1.691899\n8,1.3500892,2.4227288,0.05710747,-0.91449356,-1.3446745,-0.029760672,-0.20465523,-1.2024417\n9,1.1568894,0.78419,-1.1313103,0.10719836,-0.4748038,0.24595785,0.15343018,-0.39217895\n10,1.250678,2.2764914,-0.3198366,-0.18763481,-0.

- 업로드 ensamble_ELECTRA.csv, ensamble_BERT.csv ③

In [53]:
ensemble_ELECTRA= pd.read_csv("./ensemble_ELECTRA_eng.csv", index_col=0)
ensemble_BERT = pd.read_csv("./ensemble_BERT_eng.csv", index_col=0)

print(ensemble_ELECTRA)
print(ensemble_BERT)

             0         1         2  ...         5         6         7
0     2.608582 -2.280546 -0.944230  ...  0.665029  0.660078  0.388064
1     0.909815  2.710285 -1.251963  ... -1.630815  3.130438 -1.721149
2     3.280739  0.143322  1.279127  ...  0.052310 -0.987286 -0.988057
3     0.783259 -0.891066  4.166071  ... -0.504811  0.606540 -1.515062
4     2.611266 -1.608976 -1.230531  ...  0.464994 -1.351587  0.510723
...        ...       ...       ...  ...       ...       ...       ...
1173  0.533923  5.039102 -1.392905  ... -2.280438 -1.098461 -1.214996
1174  1.126813 -0.879095 -1.802367  ... -0.715736 -1.506538  0.491429
1175  0.062535  0.046638 -1.511013  ... -0.845089 -1.836584  0.126900
1176  0.272540 -0.216383 -1.562292  ... -0.805185 -1.953074  0.300983
1177  3.025661  0.500484  2.543828  ... -0.914751  0.319188 -1.850146

[1178 rows x 8 columns]
             0         1         2  ...         5         6         7
0     1.673975 -2.483794 -0.847334  ...  0.012789  1.219518 -0.03

- 앙상블 예측결과 Soft Voting ③

In [54]:
# 앙상블 데이터 SUM
ensemble_sum = ensemble_BERT + ensemble_ELECTRA
print(ensemble_sum)

# 앙상블 모델 수로 나누어줌
ensemble_out = ensemble_sum / 2
print(ensemble_out)

             0         1         2  ...         5         6         7
0     4.282557 -4.764340 -1.791564  ...  0.677818  1.879597  0.348328
1     1.436493  5.847667 -2.756660  ... -3.205228  6.356720 -2.871855
2     5.706922  0.906233  3.144309  ...  0.899107 -1.205226 -1.901265
3     2.228932 -2.213779  7.705044  ...  0.076120  1.858901 -2.391204
4     4.821872 -2.324858  0.787461  ... -0.093694 -2.153855  0.011146
...        ...       ...       ...  ...       ...       ...       ...
1173  1.471539  9.688970 -2.707313  ... -3.726350 -3.144527 -1.891412
1174  2.918057 -3.304543 -2.317062  ... -0.497829  0.621185  0.139225
1175  0.851980 -0.880741 -2.291271  ... -0.366651 -3.907102 -0.328421
1176  2.502588 -1.799382 -2.588783  ...  0.660888 -2.261210  0.325849
1177  5.816478  1.356694  4.496120  ... -0.916046  1.929226 -3.430544

[1178 rows x 8 columns]
             0         1         2  ...         5         6         7
0     2.141279 -2.382170 -0.895782  ...  0.338909  0.939798  0.17

- 앙상블 예측결과 Soft Voting 결과 산출 ③

In [55]:
ensemble_score = []
ensemble_score = np.array(ensemble_out)
#ensemble_score = np.delete(ensemble_score, 0, axis = 1)
ensemble_score_out = np.argmax(ensemble_score, axis = 1)
ensemble_score_out = ensemble_score_out.tolist()

print(ensemble_score_out[:100])
print(np.shape(ensemble_score_out))

[0, 6, 0, 2, 0, 1, 1, 2, 0, 6, 1, 1, 0, 0, 1, 2, 1, 1, 1, 6, 5, 6, 2, 1, 1, 2, 6, 2, 1, 1, 1, 1, 1, 0, 1, 1, 6, 1, 6, 6, 0, 1, 0, 6, 0, 0, 1, 0, 3, 0, 1, 1, 5, 2, 2, 2, 1, 1, 1, 0, 1, 1, 1, 6, 0, 2, 2, 1, 1, 6, 2, 6, 0, 0, 2, 2, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 2, 1, 1, 2, 2, 1, 3, 1, 2, 1, 1, 0, 0]
(1178,)


- 앙상블 모델 예측 결과 스코어링

In [56]:
print("Ensemble Model accuracy : ", accuracy_score(labels_test, ensemble_score_out))

Ensemble Model accuracy :  0.6103565365025467


- 앙상블 예측결과 레이블 변환 및 예측결과 산출 ③

In [57]:
def inttolabel(str):
    return { 0 : 'non-neutral',
             1 : 'neutral', 
             2 : 'joy', 
             3 : 'sadness', 
             4 : 'fear', 
             5 : 'anger', 
             6 : 'surprise', 
             7 : 'disgust'}[str]

predicted_str = []

for d in ensemble_score_out:
  predicted_str.append(inttolabel(d))

In [58]:
print(predicted_str)

['non-neutral', 'surprise', 'non-neutral', 'joy', 'non-neutral', 'neutral', 'neutral', 'joy', 'non-neutral', 'surprise', 'neutral', 'neutral', 'non-neutral', 'non-neutral', 'neutral', 'joy', 'neutral', 'neutral', 'neutral', 'surprise', 'anger', 'surprise', 'joy', 'neutral', 'neutral', 'joy', 'surprise', 'joy', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'non-neutral', 'neutral', 'neutral', 'surprise', 'neutral', 'surprise', 'surprise', 'non-neutral', 'neutral', 'non-neutral', 'surprise', 'non-neutral', 'non-neutral', 'neutral', 'non-neutral', 'sadness', 'non-neutral', 'neutral', 'neutral', 'anger', 'joy', 'joy', 'joy', 'neutral', 'neutral', 'neutral', 'non-neutral', 'neutral', 'neutral', 'neutral', 'surprise', 'non-neutral', 'joy', 'joy', 'neutral', 'neutral', 'surprise', 'joy', 'surprise', 'non-neutral', 'non-neutral', 'joy', 'joy', 'neutral', 'non-neutral', 'non-neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'neutral', 'non-neutral', 'neutral', 'neutral', 'joy', 'ne

In [59]:
ensemble_out = pd.DataFrame({'Expected' : predicted_str})
print(ensemble_out)

         Expected
0     non-neutral
1        surprise
2     non-neutral
3             joy
4     non-neutral
...           ...
1173      neutral
1174  non-neutral
1175      sadness
1176      sadness
1177  non-neutral

[1178 rows x 1 columns]


In [60]:
ensemble_out.to_csv('ensemble_submission.csv')